In [1]:
import yfinance as yf
import numpy as np
from scipy.stats import norm
import pandas as pd
from concurrent.futures import ThreadPoolExecutor, as_completed
from sklearn.ensemble import GradientBoostingRegressor
from scipy.ndimage import gaussian_filter1d
from scipy.optimize import minimize, Bounds, brentq
import plotly.offline as pyo
from sklearn.preprocessing import PolynomialFeatures
from scipy.interpolate import griddata
from scipy.ndimage import gaussian_filter, gaussian_filter1d
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import RBF, ConstantKernel as C
import plotly.graph_objs as go

import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

stocks = ['SPY', 'AAPL', 'MSFT', 'GOOGL', 'AMZN', 'TSLA', 'META', 'NVDA', 'AMD', 'NFLX', 'QQQ']
expiry_dates = ['2025-01-03', '2025-01-17', '2025-02-21', '2025-03-21', '2025-04-17', '2025-05-16']
risk_free_rate = 0.05

def get_time_to_expiry(expiry_date):
    current_date = np.datetime64('today')
    expiry_date = np.datetime64(expiry_date)
    return (expiry_date - current_date).astype('timedelta64[D]').astype(int) / 365.25

def black_scholes_price(S, K, T, r, sigma, option_type='call'):
    d1 = (np.log(S / K) + (r + 0.5 * sigma**2) * T) / (sigma * np.sqrt(T))
    d2 = d1 - sigma * np.sqrt(T)
    if option_type == 'call':
        price = S * norm.cdf(d1) - K * np.exp(-r * T) * norm.cdf(d2)
    elif option_type == 'put':
        price = K * np.exp(-r * T) * norm.cdf(-d2) - S * norm.cdf(-d1)
    return price

def calculate_iv_vectorized(midpoints, current_price, strikes, time_to_expiry, risk_free_rate, option_type='call'):
    ivs = []
    for midpoint, strike in zip(midpoints, strikes):
        try:
            iv = brentq(lambda sigma: black_scholes_price(current_price, strike, time_to_expiry, risk_free_rate, sigma, option_type) - midpoint, 1e-6, 5)
            ivs.append(iv)
        except Exception:
            ivs.append(np.nan)
    return np.array(ivs)

def fetch_option_data(stock, expiry_date):
    try:
        ticker = yf.Ticker(stock)
        current_price = ticker.history(period='1d')['Close'].iloc[-1]
        
        options = ticker.option_chain(expiry_date)
        calls = options.calls
        puts = options.puts

        otm_calls = calls[calls['strike'] > current_price][['strike', 'bid', 'ask']]
        otm_puts = puts[puts['strike'] < current_price][['strike', 'bid', 'ask']]
        
        otm_calls['moneyness'] = current_price / otm_calls['strike']
        otm_puts['moneyness'] = current_price / otm_puts['strike']
        otm_calls['midpoint'] = otm_calls['ask']
        otm_puts['midpoint'] = otm_puts['ask']
        
        otm_calls['iv_midpoint'] = calculate_iv_vectorized(otm_calls['midpoint'].values, current_price, otm_calls['strike'].values, get_time_to_expiry(expiry_date), risk_free_rate, 'call')
        otm_puts['iv_midpoint'] = calculate_iv_vectorized(otm_puts['midpoint'].values, current_price, otm_puts['strike'].values, get_time_to_expiry(expiry_date), risk_free_rate, 'put')
        
        combined_options = pd.concat([otm_calls, otm_puts])
        combined_options = combined_options[combined_options['iv_midpoint'] >= 0.001]
        combined_options['stock'] = stock
        
        return combined_options[['stock', 'moneyness', 'iv_midpoint']]
    except Exception as e:
        print(f"Error retrieving data for {stock} with expiry {expiry_date}: {e}")
        return pd.DataFrame()

# Prepare data for 3D plotting for multiple stocks
fig_stocks = go.Figure()

def fetch_volume_data(stocks):
    volumes = {}
    for stock in stocks:
        try:
            ticker = yf.Ticker(stock)
            volume = ticker.history(period='1d')['Volume'].iloc[-1]
            volumes[stock] = volume
        except Exception as e:
            print(f"Error retrieving volume data for {stock}: {e}")
            volumes[stock] = 0
    return volumes

volumes = fetch_volume_data(stocks)

for expiry_date in expiry_dates:
    time_to_expiry = get_time_to_expiry(expiry_date)
    
    options_data = []

    with ThreadPoolExecutor(max_workers=10) as executor:
        futures = {executor.submit(fetch_option_data, stock, expiry_date): stock for stock in stocks}
        for future in as_completed(futures):
            data = future.result()
            if not data.empty:
                options_data.append(data)

    if options_data:
        all_options_data = pd.concat(options_data)
        
        # Filter to include only moneyness values up to 2 and at least 0.25
        all_options_data = all_options_data[(all_options_data['moneyness'] <= 2) & (all_options_data['moneyness'] >= 0.25)]
        
        moneyness = all_options_data['moneyness'].values
        iv_midpoint = all_options_data['iv_midpoint'].values

        sorted_indices = np.argsort(moneyness)
        moneyness_sorted = moneyness[sorted_indices]
        iv_midpoint_sorted = iv_midpoint[sorted_indices]

        # Add volumes to the DataFrame and normalize
        all_options_data['volume'] = all_options_data['stock'].map(volumes)
        weights = all_options_data['volume'].values
        weights = weights / np.sum(weights)  # Normalize weights to sum to 1
        weights = weights[sorted_indices]  # Ensure weights correspond to the sorted moneyness and iv_midpoint

        # Fit PolynomialFeatures
        poly = PolynomialFeatures(degree=2)
        moneyness_poly = poly.fit_transform(moneyness_sorted.reshape(-1, 1))

        # Gaussian Process Regressor with RBF kernel
        kernel = C(1.0, (1e-4, 1e1)) * RBF(length_scale=1.0, length_scale_bounds=(1e-4, 1e1))
        gpr = GaussianProcessRegressor(kernel=kernel, n_restarts_optimizer=10, alpha=1e-2)
        gpr.fit(moneyness_poly, iv_midpoint_sorted)

        x_vals = np.linspace(min(moneyness_sorted), max(moneyness_sorted), 500)
        x_vals_poly = poly.transform(x_vals.reshape(-1, 1))  # Apply polynomial features
        y_vals_gpr, sigma = gpr.predict(x_vals_poly, return_std=True)

        # Apply Gaussian smoothing
        y_vals_smoothed = gaussian_filter1d(y_vals_gpr, sigma=2)

        # Add trace for the current expiry date
        fig_stocks.add_trace(go.Scatter3d(
            x=x_vals,
            y=[time_to_expiry] * len(x_vals),
            z=y_vals_smoothed,
            mode='lines',
            name=f'Expiry {expiry_date}',
            line=dict(width=2)
        ))

        # Add data points for the current expiry date
        fig_stocks.add_trace(go.Scatter3d(
            x=moneyness_sorted,
            y=[time_to_expiry] * len(moneyness_sorted),
            z=iv_midpoint_sorted,
            mode='markers',
            name=f'Data Points {expiry_date}',
            marker=dict(size=4)
        ))

# Layout for the 3D plot
fig_stocks.update_layout(
    title='Implied Volatility Surfaces for Different Expiry Dates (Multiple Stocks)',
    scene=dict(
        xaxis_title='Moneyness',
        yaxis_title='Time to Expiry (Years)',
        zaxis_title='Implied Volatility',
    )
)

# Show plot
pyo.iplot(fig_stocks)

Error retrieving data for NFLX with expiry 2025-04-17: Expiration `2025-04-17` cannot be found. Available expirations are: [2025-01-03, 2025-01-10, 2025-01-17, 2025-01-24, 2025-01-31, 2025-02-21, 2025-03-21, 2025-06-20, 2025-08-15, 2025-09-19, 2025-12-19, 2026-01-16, 2026-12-18, 2027-01-15]
Error retrieving data for QQQ with expiry 2025-04-17: Expiration `2025-04-17` cannot be found. Available expirations are: [2024-12-30, 2024-12-31, 2025-01-02, 2025-01-03, 2025-01-10, 2025-01-17, 2025-01-24, 2025-01-31, 2025-02-21, 2025-02-28, 2025-03-21, 2025-03-31, 2025-06-20, 2025-06-30, 2025-09-19, 2025-09-30, 2025-12-19, 2026-01-16, 2026-06-18, 2026-09-18, 2026-12-18, 2027-01-15]
Error retrieving data for AAPL with expiry 2025-05-16: Expiration `2025-05-16` cannot be found. Available expirations are: [2025-01-03, 2025-01-10, 2025-01-17, 2025-01-24, 2025-01-31, 2025-02-21, 2025-03-21, 2025-04-17, 2025-06-20, 2025-07-18, 2025-08-15, 2025-09-19, 2025-12-19, 2026-01-16, 2026-06-18, 2026-12-18, 2027-

In [2]:
# Prepare data for 3D plotting for LMT 
fig_lmt = go.Figure()

all_moneyness = []
all_time_to_expiry = []
all_iv_actual = []

for expiry_date in expiry_dates:
    time_to_expiry = get_time_to_expiry(expiry_date)

    def fetch_lmt_option_data(expiry_date):
        try:
            stock = 'LMT'
            ticker = yf.Ticker(stock)
            current_price = ticker.history(period='1d')['Close'].iloc[-1]
            
            options = ticker.option_chain(expiry_date)
            calls = options.calls
            puts = options.puts

            otm_calls = calls[calls['strike'] > current_price][['strike', 'bid', 'ask']]
            otm_puts = puts[puts['strike'] < current_price][['strike', 'bid', 'ask']]
            
            otm_calls['moneyness'] = current_price / otm_calls['strike']
            otm_puts['moneyness'] = current_price / otm_puts['strike']
            otm_calls['midpoint'] = otm_calls['ask']
            otm_puts['midpoint'] = otm_puts['ask']

            otm_calls['iv_midpoint'] = calculate_iv_vectorized(otm_calls['midpoint'].values, current_price, otm_calls['strike'].values, get_time_to_expiry(expiry_date), risk_free_rate, 'call')
            otm_puts['iv_midpoint'] = calculate_iv_vectorized(otm_puts['midpoint'].values, current_price, otm_puts['strike'].values, get_time_to_expiry(expiry_date), risk_free_rate, 'put')
            
            combined_options = pd.concat([otm_calls, otm_puts])
            combined_options = combined_options[combined_options['iv_midpoint'] >= 0.001]
            combined_options['stock'] = stock
            
            return combined_options[['stock', 'moneyness', 'iv_midpoint', 'midpoint', 'strike']]
        except Exception as e:
            print(f"Error retrieving data for LMT with expiry {expiry_date}: {e}")
            return pd.DataFrame()

    lmt_data = fetch_lmt_option_data(expiry_date)

    if not lmt_data.empty:
        lmt_moneyness = lmt_data['moneyness'].values
        lmt_iv_actual = lmt_data['iv_midpoint'].values
        
        # Remove NaN values from lmt_iv_actual and corresponding lmt_moneyness
        valid_indices = ~np.isnan(lmt_iv_actual)
        lmt_moneyness = lmt_moneyness[valid_indices]
        lmt_iv_actual = lmt_iv_actual[valid_indices]
        
        # Limit the moneyness values to the range [0.25, 2]
        within_range_indices = (lmt_moneyness >= 0.25) & (lmt_moneyness <= 2)
        lmt_moneyness = lmt_moneyness[within_range_indices]
        lmt_iv_actual = lmt_iv_actual[within_range_indices]
        
        # Transform x_vals using polynomial features for model fitting
        poly = PolynomialFeatures(degree=2)
        x_vals_poly = poly.fit_transform(x_vals.reshape(-1, 1))

        # Adjust the function to include weights more aggressively
        def robust_alignment_error(transforms, x_vals, y_vals_smoothed, lmt_moneyness, lmt_iv_actual):
            scale, horizontal_shift, vertical_shift, stretch_factor = transforms
            adjusted_x_vals = x_vals * scale + horizontal_shift
            adjusted_y_vals_smoothed = y_vals_smoothed * stretch_factor + vertical_shift
            interpolated_iv = np.interp(lmt_moneyness, adjusted_x_vals, adjusted_y_vals_smoothed)
            
            # Calculate weights more aggressively based on the distance of moneyness from 1
            weights = 1 / (np.abs(lmt_moneyness - 1) + 0.1)  # Adding a small constant to avoid division by zero
            weights = weights / np.max(weights)  # Normalize weights to be between 0 and 1
            
            error = np.sum(weights * np.abs(interpolated_iv - lmt_iv_actual))  # Weighted L1 norm
            return error

        # Initial guesses for the transforms (scale, horizontal shift, vertical shift, stretch_factor)
        initial_transforms = [1, 0, 0, 1]
        
        # Bounds for the optimization
        bounds = Bounds([0.1, -0.1, -np.inf, 0.1], [10, 0.1, np.inf, 10])
        

        # Perform the optimization using the robust error metric
        result = minimize(robust_alignment_error, initial_transforms, args=(x_vals, y_vals_smoothed, lmt_moneyness, lmt_iv_actual), bounds=bounds)

        # Extract the optimized transforms
        optimized_scale, optimized_horizontal_shift, optimized_vertical_shift, optimized_stretch_factor = result.x

        # Apply the optimized transforms to the original x_vals and y_vals_smoothed
        adjusted_x_vals = x_vals * optimized_scale + optimized_horizontal_shift
        adjusted_y_vals_smoothed = y_vals_smoothed * optimized_stretch_factor + optimized_vertical_shift
        
        # Store data for surface plot
        all_moneyness.extend(adjusted_x_vals)
        all_time_to_expiry.extend([time_to_expiry] * len(adjusted_x_vals))
        all_iv_actual.extend(adjusted_y_vals_smoothed)

        # Add the optimized trace for LMT
        fig_lmt.add_trace(go.Scatter3d(
            x=adjusted_x_vals,
            y=[time_to_expiry] * len(adjusted_x_vals),
            z=adjusted_y_vals_smoothed,
            mode='lines',
            name=f'Optimized GBR Fit {expiry_date}',
            line=dict(width=2)
        ))

        # Add LMT actual data points
        fig_lmt.add_trace(go.Scatter3d(
            x=lmt_moneyness,
            y=[time_to_expiry] * len(lmt_moneyness),
            z=lmt_iv_actual,
            mode='markers',
            name=f'LMT Actual Data {expiry_date}',
            marker=dict(size=4, color='blue')
        ))

        # Layout for the 3D plot for LMT with increased size
        fig_lmt.update_layout(
            title='Implied Volatility Surfaces for Different Expiry Dates (NXPI)',
            scene=dict(
                xaxis_title='Moneyness',
                yaxis_title='Time to Expiry (Years)',
                zaxis_title='Implied Volatility',
            ),
            width=1000,  # Adjust width as needed
            height=1200   # Adjust height as needed
        )

# Show plot
pyo.iplot(fig_lmt)

Error retrieving data for LMT with expiry 2025-04-17: Expiration `2025-04-17` cannot be found. Available expirations are: [2025-01-03, 2025-01-10, 2025-01-17, 2025-01-24, 2025-01-31, 2025-02-21, 2025-03-21, 2025-06-20, 2025-09-19, 2026-01-16, 2026-12-18, 2027-01-15]
Error retrieving data for LMT with expiry 2025-05-16: Expiration `2025-05-16` cannot be found. Available expirations are: [2025-01-03, 2025-01-10, 2025-01-17, 2025-01-24, 2025-01-31, 2025-02-21, 2025-03-21, 2025-06-20, 2025-09-19, 2026-01-16, 2026-12-18, 2027-01-15]


In [5]:
fig_surface = go.Figure()


# Convert lists to arrays for creating the surface plot
all_moneyness = np.array(all_moneyness)
all_time_to_expiry = np.array(all_time_to_expiry)
all_iv_actual = np.array(all_iv_actual)

# Filter out points with IV above 1
valid_indices = all_iv_actual <= 1
filtered_moneyness = all_moneyness[valid_indices]
filtered_time_to_expiry = all_time_to_expiry[valid_indices]
filtered_iv_actual = all_iv_actual[valid_indices]

# Create a grid for interpolation
grid_x, grid_y = np.meshgrid(
    np.linspace(filtered_moneyness.min(), filtered_moneyness.max(), 200),
    np.linspace(filtered_time_to_expiry.min(), filtered_time_to_expiry.max(), 200)
)

# Interpolate the data
grid_z = griddata(
    (filtered_moneyness, filtered_time_to_expiry),
    filtered_iv_actual,
    (grid_x, grid_y),
    method='linear'
)

# Apply Gaussian smoothing
grid_z_smoothed = gaussian_filter(grid_z, sigma=1)

# Create the surface plot
fig_surface = go.Figure()

fig_surface.add_trace(go.Surface(
    x=grid_x,
    y=grid_y,
    z=grid_z_smoothed,
    colorscale='Blues_r',
    showscale=True,
    opacity=0.75,  # Set the transparency here
    contours={
        "x": {"show": False, "color": "white", "size": 0.1},
        "y": {"show": False, "color": "white", "size": 0.1},
        "z": {"show": True, "color": "white", "size": 0.1}
    }
))

# Layout for the 3D surface plot for LMT
fig_surface.update_layout(
    title='Implied Volatility Surfaces for Different Expiry Dates (LMT)',
    scene=dict(
        xaxis=dict(
            title='Moneyness',
            showticklabels=True,
            showgrid=True,
            gridcolor='gray',
            gridwidth=1,
            nticks=20  # Define the number of grid lines
        ),
        yaxis=dict(
            title='Time to Expiry (Years)',
            showticklabels=True,
            showgrid=True,
            gridcolor='gray',
            gridwidth=1,
            nticks=20  # Define the number of grid lines
        ),
        zaxis=dict(
            title='Implied Volatility',
            showticklabels=True,
            showgrid=True,
            gridcolor='gray',
            gridwidth=1,
            nticks=50  # Define the number of grid lines
        ),
        aspectratio=dict(x=1, y=1, z=0.5)  # Adjust the z-axis aspect ratio
    ),
    autosize=False,
    width=1200,
    height=1200,
)

# Show plot
fig_surface.show()